## Import the Libraries

In [6]:
import geopandas as gpd
import geojson
import json
from OSMPythonTools.nominatim import Nominatim
from OSMPythonTools.overpass import Overpass, overpassQueryBuilder
from OSMPythonTools.api import Api
import folium
from folium.plugins import TimestampedGeoJson

import seaborn as sns
import missingno as msno
%matplotlib inline

## Import the Dataset

In [2]:
df_accessible = gpd.read_file("../data/datathon/parking/parking_spaces_for_disabled_persons.geojson").astype({"ANZAHL": "int64"})

In [4]:
df_acc = df_accessible[["ANZAHL", "BEMERKUNG", "geometry"]]
df_acc.columns = ["count", "open", "geometry"]
df_acc["fillColor"] = "#54c699"
df_acc.head()

/Users/lelischiestl/opt/anaconda3/envs/dssg/lib/python3.9/site-packages/geopandas/geodataframe.py:1351: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


count            open                   geometry fillColor
0      1     Durchgehend  POINT (13.47776 52.49258)   #54c699
1      1  Mo-Fr 7-20.30h  POINT (13.46786 52.49573)   #54c699
2      1     Mo-Fr 7-17h  POINT (13.39625 52.49921)   #54c699
3      1    Mo-Fr 10-21h  POINT (13.39887 52.50772)   #54c699
4      1     Mo-Fr 8-18h  POINT (13.39943 52.50848)   #54c699

## Create Functions

In [5]:
def create_geojson_features(df, timestamp):
    features = []

    for _, row in df.iterrows():
        feature = {
            "type": "Feature",
            "geometry": {
                "type": "Point",
                "coordinates": [row.geometry.x, row.geometry.y]
            },
            "properties": {
                "times": [timestamp],
                "style": {
                    "color": "red"
                },
                "icon": "circle",
                "iconstyle": {
                    "fillColor": row["fillColor"],
                    "fillOpacity": 0.8,
                    "stroke": "true",
                    "radius": 3
                }
            }
        }
        features.append(feature)
    return features


In [8]:
from datetime import datetime, timedelta

def daterange(start_date, end_date):
    for n in range(int((end_date - start_date).days * 24)):
        yield start_date + timedelta(hours=n)

start_date = datetime(2021, 1, 4)
end_date = datetime(2021, 1, 11)


In [12]:
def create_geojson_point(x, y, time):
    geojson_point = {
        "type": "Feature",
        "properties": {
            'style': {
            'color': 'blue',
            },
            'times': [time],
            "style": {
                "color": "red"
            },
            "icon": "circle",
            "iconstyle": {
                "fillColor": "#586065",
                "fillOpacity": 0.8,
                "stroke": "true",
                "radius": 3
            }
        },
        "geometry": {
            "type": "Point",
            "coordinates": [x, y]}
    }
    return geojson_point

In [10]:
def create_geojson_features(df):
    features = []
    for _, row in df.iterrows():
        for single_datetime in daterange(datetime(2021,1,4), datetime(2021,1,11)):
            if row.open == "Durchgehend":
                features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 7-20.30h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 7 and int(single_datetime.hour) <= 21:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 7-17h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 7 and int(single_datetime.hour) <= 17:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 10-21h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 10 and int(single_datetime.hour) <= 21:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 8-18h" or row.open == "Mo-Fr  8-18h" or row.open == "Mo-Fr 8.30-18h" or row.open == "Mo-Fr 8-18h + Zusatz Parkscheibe 2h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 18:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 8-17h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 17:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 8-16h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 16:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 8-19h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 19:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Sa 8-16h, So 9-18h":
                if single_datetime.weekday() == 5 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 16 or single_datetime.weekday() == 6 and int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 18 :
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "(täglich) 9-22h":
                if int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 22:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 12-18h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 12 and int(single_datetime.hour) <= 18:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr  7-16h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 7 and int(single_datetime.hour) <= 16:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo - Fr 9-18h, Sa 9-14h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 18 or single_datetime.weekday() == 5 and int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 14:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Do 7-19h, Fr 7-16h":
                if single_datetime.weekday() < 4 and int(single_datetime.hour) >= 7 and int(single_datetime.hour) <= 19 or single_datetime.weekday() == 5 and int(single_datetime.hour) >= 7 and int(single_datetime.hour) <= 16:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Do-So 15-22h":
                if single_datetime.weekday() > 2 and int(single_datetime.hour) >= 15 and int(single_datetime.hour) <= 22:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 9-16h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 16:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 7-16h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 7 and int(single_datetime.hour) <= 16:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 9-18h, Sa 9-14h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 18 or single_datetime.weekday() == 5 and int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 14:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 8-20h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 20:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr  6-18h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 6 and int(single_datetime.hour) <= 18:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 9-21h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 21:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 9-18h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 18:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "(täglich) 19-23h":
                if int(single_datetime.hour) >= 19 and int(single_datetime.hour) <= 23:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 7-20h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 7 and int(single_datetime.hour) <= 20:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "werktags 7-18h" or row.open == "Mo-Fr 7-18h" or row.open == "Mo-Fr 7.30-18h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 7 and int(single_datetime.hour) <= 18:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 13-19h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 13 and int(single_datetime.hour) <= 19:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Do 8-18h, Fr 8-13h":
                if single_datetime.weekday() < 4 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 18 or single_datetime.weekday() == 4 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 13:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 8-18h, Sa 9-16h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 18 or single_datetime.weekday() == 5 and int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 16:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo Fr 8-16h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 16:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 6-18h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 6 and int(single_datetime.hour) <= 18:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "(täglich) 9-20h":
                if int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 20:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Do 8-17h, Fr 8-15h":
                if single_datetime.weekday() < 4 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 17 or single_datetime.weekday() == 4 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 15:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 6.30-20h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 6 and int(single_datetime.hour) <= 20:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 9-18h, Sa 9-13h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 18 or single_datetime.weekday() == 5 and int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 13:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 7-19h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 7 and int(single_datetime.hour) <= 19:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 9-20h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 20:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 6-19.30h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 6 and int(single_datetime.hour) <= 20:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 7-15h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 7 and int(single_datetime.hour) <= 15:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 10-20h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 10 and int(single_datetime.hour) <= 20:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 6-8h, 13-15h":
                if single_datetime.weekday() < 5 and (int(single_datetime.hour) >= 6 and int(single_datetime.hour) <= 8 or int(single_datetime.hour) >= 13 and int(single_datetime.hour) <= 15):
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-So 9-21h":
                if int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 21:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 8-19h, Sa 8-16h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 19 or single_datetime.weekday() == 5 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 16:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Sonn- u. Feiertags 10-13h":
                if single_datetime.weekday() >= 5 and int(single_datetime.hour) >= 10 and int(single_datetime.hour) <= 13:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 8.30-18h, Sa 9-11h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 18 or single_datetime.weekday() == 5 and int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 11:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "(täglich) 9-23h":
                if int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 23:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "(täglich) 18-23h":
                if int(single_datetime.hour) >= 18 and int(single_datetime.hour) <= 23:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mi 18-21h, So 9-12h und 18-21h":
                if single_datetime.weekday() == 2 and int(single_datetime.hour) >= 18 and int(single_datetime.hour) <= 21 or single_datetime.weekday() == 6 and (int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 12 or int(single_datetime.hour) >= 18 and int(single_datetime.hour) <= 21) :
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 8-21h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 21:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 9-18h, Sa 9 -14h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 18 or single_datetime.weekday() == 5 and int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 14:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "während der Öffnungszeiten Bezirksamtes":
                if single_datetime.weekday() == 0 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 15 or (single_datetime.weekday() == 1 or single_date.weekday() == 3) and (int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 12 or int(single_datetime.hour) >= 13 and int(single_datetime.hour) <= 18) or single_datetime.weekday() == 2 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 14 or  single_datetime.weekday() == 4 and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 13:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 7.30-19.30h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 7 and int(single_datetime.hour) <= 19:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo,Di,Do,Fr 8-14h, Mi 14-18h":
                if single_datetime.weekday() in (0, 1, 3, 4) and int(single_datetime.hour) >= 8 and int(single_datetime.hour) <= 14 or single_datetime.weekday() == 2 and int(single_datetime.hour) >= 14 and int(single_datetime.hour) <= 18:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-So 9-20h":
                if int(single_datetime.hour) >= 9 and int(single_datetime.hour) <= 20:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            elif row.open == "Mo-Fr 10-17h":
                if single_datetime.weekday() < 5 and int(single_datetime.hour) >= 10 and int(single_datetime.hour) <= 17:
                    features.append(create_geojson_point(row.geometry.x, row.geometry.y, single_datetime.strftime("%Y-%m-%dT%H:%M:%S")))
            else:
                print("!!!!!!!")


        #feature = create_geojson_point(row.geometry.x, row.geometry.y, time)
        #features.append(feature)
    return features

In [13]:
features = create_geojson_features(df_acc)

In [14]:

m = folium.Map(
    location=[52.51, 13.45],
    zoom_start=13.3,
    tiles="openstreetmap"
)

TimestampedGeoJson(
    {'type': 'FeatureCollection', 'features': features},
    period='PT1H',
    duration='PT1H',
    auto_play=True,
    loop=True,
    loop_button=True,
    #date_options='YYYY/MM/DD',
    date_options="dddd HH:mm"
).add_to(m)

m